# TCGA-UCEC – Notebook 0A
## Acquisition des données brutes (GDC/TCGA)

**Objectif** : Télécharger les données de comptage STAR et les métadonnées cliniques via l'API du GDC en utilisant l'interopérabilité R-Python. Cette étape garantit la provenance et la reproductibilité des données sources.

## 1. Configuration et Environnement

In [1]:
# ==========================================================================================================
import os                                       # Navigation fichiers (DIRS, chemins relatifs)
import sys                                      # Interaction système
import pandas as pd                             # Manipulation de tables
import subprocess                               # Exécution de commandes avec streaming de sortie

# ==========================================================================================================
# Définition de la racine du projet
PROJECT_ROOT = os.getcwd()

DIRS = {
    "RAW":       os.path.join(PROJECT_ROOT, "data", "raw"),
    "SCRIPTS":   os.path.join(PROJECT_ROOT, "scripts"),
    "PROCESSED": os.path.join(PROJECT_ROOT, "data", "processed")
}

for path in DIRS.values():
    os.makedirs(path, exist_ok=True)

# ==========================================================================================================
print(f"✅ Environnement configuré. Racine : {PROJECT_ROOT}")
print(f"✅ Dossiers d'acquisition prêts.")

✅ Environnement configuré. Racine : c:\Z\M2_AIDA\TCGA_UCEC_project
✅ Dossiers d'acquisition prêts.


## 2. Exécution du script d'acquisition (Rscript)

Le téléchargement s'appuie sur la librairie R **TCGAbiolinks**. Nous appelons le script fourni directement depuis ce notebook pour maintenir une traçabilité complète.

In [2]:
# ==========================================================================================================
# Chemin vers l'exécutable R et le script moteur
R_EXECUTABLE = r"C:\Program Files\R\R-4.5.2\bin\x64\Rscript.exe"
r_script_path = os.path.join(DIRS["SCRIPTS"], "Script_data_download.R")

if os.path.exists(r_script_path):
    print("⏳ Acquisition en cours : téléchargement depuis le GDC (cela peut prendre 5-10 minutes)...\n")
    
    # Appel système à Rscript
    # Utilisation de subprocess pour capturer et afficher la sortie de R en temps réel
    process = subprocess.Popen(
        [R_EXECUTABLE, r_script_path], 
        stdout=subprocess.PIPE, 
        stderr=subprocess.STDOUT, 
        text=True,
        encoding='utf-8'
    )

    # Lecture de la sortie ligne par ligne pour un retour utilisateur immédiat
    for line in process.stdout:
        print(line, end='')

    process.wait()
    
    if process.returncode == 0:
        print("\n✅ Script R terminé avec succès. Données prêtes dans data/raw/.")
    else:
        print(f"\nErreur lors de l'exécution du script R (Code retour: {process.returncode})")
else:
    print(f"Fichier script R introuvable : {r_script_path}")

⏳ Acquisition en cours : téléchargement depuis le GDC (cela peut prendre 5-10 minutes)...

Le chargement a nécessité le package : MatrixGenerics
Le chargement a nécessité le package : matrixStats

Attachement du package : 'MatrixGenerics'

Les objets suivants sont masqués depuis 'package:matrixStats':

    colAlls, colAnyNAs, colAnys, colAvgsPerRowSet, colCollapse,
    colCounts, colCummaxs, colCummins, colCumprods, colCumsums,
    colDiffs, colIQRDiffs, colIQRs, colLogSumExps, colMadDiffs,
    colMads, colMaxs, colMeans2, colMedians, colMins, colOrderStats,
    colProds, colQuantiles, colRanges, colRanks, colSdDiffs, colSds,
    colSums2, colTabulates, colVarDiffs, colVars, colWeightedMads,
    colWeightedMeans, colWeightedMedians, colWeightedSds,
    colWeightedVars, rowAlls, rowAnyNAs, rowAnys, rowAvgsPerColSet,
    rowCollapse, rowCounts, rowCummaxs, rowCummins, rowCumprods,
    rowCumsums, rowDiffs, rowIQRDiffs, rowIQRs, rowLogSumExps,
    rowMadDiffs, rowMads, rowMaxs, rowMeans2,

## 2Bis. Relocalisation des fichiers (Workaround Post-Acquisition)

Le script R exporte par défaut dans un dossier nommé tcga_ucec_counts_export. Nous déplaçons ces fichiers vers data/raw/ pour respecter l'arborescence du projet et permettre aux notebooks suivants d'accéder aux données.

In [ ]:
import shutil

# Chemins source et cible (os est déjà importé en cellule 1)
source_dir = os.path.join(PROJECT_ROOT, "tcga_ucec_counts_export")
target_dir = DIRS["RAW"]

files_to_move = [
    "counts_samples_x_genes.csv.gz",
    "metadata_clinical_merged.csv.gz",
    "gene_annotation.csv.gz"
]

if os.path.exists(source_dir):
    print(f"📂 Dossier source détecté : {source_dir}")
    moved_count = 0

    for f in files_to_move:
        src_path = os.path.join(source_dir, f)
        dst_path = os.path.join(target_dir, f)
        
        if os.path.exists(src_path):
            shutil.move(src_path, dst_path)
            print(f"✅ Déplacé : {f}")
            moved_count += 1
            
    if moved_count > 0:
        print(f"\n✅ Harmonisation terminée. {moved_count} fichiers déplacés vers {target_dir}.")
else:
    # Vérification de sécurité si les fichiers sont déjà là (évite de planter au re-run)
    if all(os.path.exists(os.path.join(target_dir, f)) for f in files_to_move):
        print("✅ Les fichiers sont déjà correctement placés dans data/raw/.")
    else:
        print(f"❌ Erreur : Dossier source {source_dir} introuvable et fichiers absents de {target_dir}.")

📂 Dossier source détecté : c:\Z\M2_AIDA\TCGA_UCEC_project\tcga_ucec_counts_export
✅ Déplacé : counts_samples_x_genes.csv.gz
✅ Déplacé : metadata_clinical_merged.csv.gz
✅ Déplacé : gene_annotation.csv.gz

✅ Harmonisation terminée. 3 fichiers déplacés vers c:\Z\M2_AIDA\TCGA_UCEC_project\data\raw.


## 3. Vérification des fichiers téléchargés

Contrôle de la présence physique des fichiers dans `data/raw/` et affichage des dimensions brutes.

In [4]:
# ==========================================================================================================
# Définition des chemins vers les fichiers attendus dans data/raw/
expr_file = os.path.join(DIRS["RAW"], "counts_samples_x_genes.csv.gz")
meta_file = os.path.join(DIRS["RAW"], "metadata_clinical_merged.csv.gz")

# Vérification de l'existence et chargement des données brutes
if os.path.exists(expr_file) and os.path.exists(meta_file):
    print("⏳ Lecture des fichiers compressés (cela peut prendre quelques secondes)...")
    
    # Lecture avec pandas (gestion native du .gz)
    # index_col=0 car la première colonne contient les barcodes/identifiants
    df_expr = pd.read_csv(expr_file, index_col=0)
    df_meta = pd.read_csv(meta_file, index_col=0)
    
    print(f"\n✅ Vérification terminée avec succès.")
    print(f"   - Matrice de Counts : {df_expr.shape[0]} échantillons x {df_expr.shape[1]} gènes")
    print(f"   - Métadonnées       : {df_meta.shape[0]} échantillons x {df_meta.shape[1]} colonnes cliniques")
    
    # Affichage des premières lignes pour inspection visuelle
    display(df_expr.head(3))
else:
    print(f"❌ Erreur : Fichiers introuvables dans {DIRS['RAW']}.")
    print("Veuillez vérifier que la cellule 2Bis (Relocalisation) a bien été exécutée.")

⏳ Lecture des fichiers compressés (cela peut prendre quelques secondes)...

✅ Vérification terminée avec succès.
   - Matrice de Counts : 553 échantillons x 60660 gènes
   - Métadonnées       : 553 échantillons x 175 colonnes cliniques


ENSG00000000003.15  ENSG00000000005.6  \
sample_barcode                                                        
TCGA-EY-A1GK-01A-11R-A13S-07                1904                  2   
TCGA-FI-A2CX-01A-11R-A17B-07                 496                  1   
TCGA-AX-A3G3-01A-11R-A213-07                2115                  2   

                              ENSG00000000419.13  ENSG00000000457.14  \
sample_barcode                                                         
TCGA-EY-A1GK-01A-11R-A13S-07                 607                 529   
TCGA-FI-A2CX-01A-11R-A17B-07                 839                 253   
TCGA-AX-A3G3-01A-11R-A213-07                2657                 352   

                              ENSG00000000460.17  ENSG00000000938.13  \
sample_barcode                                                         
TCGA-EY-A1GK-01A-11R-A13S-07                 138                 167   
TCGA-FI-A2CX-01A-11R-A17B-07                 194                4301   
TCGA-AX-A3G3-01A-11R-A213-07                 284                 673   

                              ENSG00000000971.16  ENSG00000001036.14  \
sample_barcode                                                         
TCGA-EY-A1GK-01A-11R-A13S-07                 238                1427   
TCGA-FI-A2CX-01A-11R-A17B-07                 847                3321   
TCGA-AX-A3G3-01A-11R-A213-07                 952                1760   

                              ENSG00000001084.13  ENSG00000001167.14  ...  \
sample_barcode                                                        ...   
TCGA-EY-A1GK-01A-11R-A13S-07                 597                 877  ...   
TCGA-FI-A2CX-01A-11R-A17B-07                2903                1147  ...   
TCGA-AX-A3G3-01A-11R-A213-07                1092                1317  ...   

                              ENSG00000288661.1  ENSG00000288662.1  \
sample_barcode                                                       
TCGA-EY-A1GK-01A-11R-A13S-07                  0                  1   
TCGA-FI-A2CX-01A-11R-A17B-07                  0                  1   
TCGA-AX-A3G3-01A-11R-A213-07                  0                  0   

                              ENSG00000288663.1  ENSG00000288665.1  \
sample_barcode                                                       
TCGA-EY-A1GK-01A-11R-A13S-07                 20                  0   
TCGA-FI-A2CX-01A-11R-A17B-07                 18                  0   
TCGA-AX-A3G3-01A-11R-A213-07                  7                  0   

                              ENSG00000288667.1  ENSG00000288669.1  \
sample_barcode                                                       
TCGA-EY-A1GK-01A-11R-A13S-07                  0                  0   
TCGA-FI-A2CX-01A-11R-A17B-07                  0                  3   
TCGA-AX-A3G3-01A-11R-A213-07                  0                  2   

                              ENSG00000288670.1  ENSG00000288671.1  \
sample_barcode                                                       
TCGA-EY-A1GK-01A-11R-A13S-07                 68                  0   
TCGA-FI-A2CX-01A-11R-A17B-07                 85                  0   
TCGA-AX-A3G3-01A-11R-A213-07                101                  0   

                              ENSG00000288674.1  ENSG00000288675.1  
sample_barcode                                                      
TCGA-EY-A1GK-01A-11R-A13S-07                  2                 44  
TCGA-FI-A2CX-01A-11R-A17B-07                  9                  7  
TCGA-AX-A3G3-01A-11R-A213-07                 13                129  

[3 rows x 60660 columns]

## 4. Prochaines étapes
- Nettoyage des noms de gènes (Mapping ENSG -> Symbol).
- Filtrage de l'expression faible (Low counts).
- Normalisation Log-CPM.
